In [1]:
import re
import numpy as np
from pyvi import ViTokenizer
from string import punctuation
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import LabelEncoder
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.linear_model import SGDClassifier
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.naive_bayes import MultinomialNB

## 1. Data Pre-processing

- Load trainning data: trainning.txt

In [2]:
with open('trainning.txt', encoding='utf8') as file:
    data = file.read()

In [3]:
data_split = data.split('\n')

data_split

['__CTXH__\tGần 500 học sinh phải học trong điều kiện tạm bợ (NLĐ)- Gần 500 học sinh Trường Tiểu học Đống Đa, P. 25, quận Bình Thạnh- TPHCM đến nay vẫn phải được gởi học tạm tại 2 nơi cách nhà khoảng 5 km do ngôi trường này đã xuống cấp trầm trọng. Theo kế hoạch, đầu năm học 2005-2006, Trường Tiểu học Đống Đa được khởi công xây dựng để sang năm các em có chỗ học, nhưng điều đáng nói là đến nay, năm học gần kết thúc, vẫn chưa thấy xây trường. Nhiều phụ huynh cảm thấy không yên tâm khi hằng ngày con em họ phải học trong tình trạng trường lớp tạm bợ và đi lại kém an toàn như thế. ',
 '__CTXH__\tNgầm hóa các công trình hạ tầng kỹ thuật Theo đó, UBND TP chấp thuận giao Khu quản lý giao thông đô thị số 1 phối hợp các đơn vị quản lý chuyên ngành di dời, tái lập các công trình hạ tầng kỹ thuật thuộc phạm vi qui hoạch xây dựng của dự án theo phương án ngầm hóa riêng biệt từng loại công trình (cáp quang bưu điện - truyền thông, điện lực, cấp nước...). UBND TP cũng chấp thuận cho Bưu điện TP nghi

- Remove label from trainning

In [4]:
label_data =  re.findall(r"(__\w+__)", data)

len(label_data)

5000

In [5]:
label_data

['__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',
 '__CTXH__',

- Vietnamese processing by ViTokenizer

In [6]:
text_data =[]
for i in range(len(label_data)):
    e = data_split[i].replace(label_data[i], "")
    e = e.replace('\t', '')
    text_lower = e.lower()
    text_token = ViTokenizer.tokenize(text_lower)
    text_data.insert(i, text_token)
    
len(text_data)

5000

In [7]:
text_data

['gần 500 học_sinh phải học trong điều_kiện tạm_bợ ( nlđ ) - gần 500 học_sinh trường tiểu_học đống đa , p . 25 , quận bình_thạnh - tphcm đến nay vẫn phải được gởi học tạm tại 2 nơi cách nhà khoảng 5 km do ngôi trường này đã xuống_cấp trầm_trọng . theo kế_hoạch , đầu năm_học 2005 - 2006 , trường tiểu_học đống đa được khởi_công xây_dựng để sang năm các em có chỗ học , nhưng điều đáng nói là đến nay , năm_học gần kết_thúc , vẫn chưa thấy xây trường . nhiều phụ_huynh cảm_thấy không yên_tâm khi hằng ngày con_em họ phải học trong tình_trạng trường lớp tạm_bợ và đi_lại kém an_toàn như thế .',
 'ngầm_hóa các công_trình hạ_tầng kỹ_thuật theo đó , ubnd tp chấp_thuận giao khu quản_lý giao_thông đô_thị số 1 phối_hợp các đơn_vị quản_lý chuyên_ngành di_dời , tái_lập các công_trình hạ_tầng kỹ_thuật thuộc phạm_vi qui_hoạch xây_dựng của dự_án theo phương_án ngầm_hóa riêng_biệt từng loại công_trình ( cáp_quang bưu_điện - truyền_thông , điện_lực , cấp_nước ... ) . ubnd tp cũng chấp_thuận cho bưu_điện tp 

- Stop words removing

In [8]:
stop_word = []
with open("stopwords.txt",encoding="utf-8") as f :
    text = f.read()
    for word in text.split() :
      stop_word.append(word)
    f.close()
    punc = list(punctuation)
stop_word = stop_word + punc

In [9]:
stop_word

['a',
 'lô',
 'a',
 'ha',
 'ai',
 'ai',
 'ai',
 'ai',
 'nấy',
 'ai',
 'đó',
 'alô',
 'amen',
 'anh',
 'anh',
 'ấy',
 'ba',
 'ba',
 'ba',
 'ba',
 'bản',
 'ba',
 'cùng',
 'ba',
 'họ',
 'ba',
 'ngày',
 'ba',
 'ngôi',
 'ba',
 'tăng',
 'bao',
 'giờ',
 'bao',
 'lâu',
 'bao',
 'nhiêu',
 'bao',
 'nả',
 'bay',
 'biến',
 'biết',
 'biết',
 'bao',
 'biết',
 'bao',
 'nhiêu',
 'biết',
 'chắc',
 'biết',
 'chừng',
 'nào',
 'biết',
 'mình',
 'biết',
 'mấy',
 'biết',
 'thế',
 'biết',
 'trước',
 'biết',
 'việc',
 'biết',
 'đâu',
 'biết',
 'đâu',
 'chừng',
 'biết',
 'đâu',
 'đấy',
 'biết',
 'được',
 'buổi',
 'buổi',
 'làm',
 'buổi',
 'mới',
 'buổi',
 'ngày',
 'buổi',
 'sớm',
 'bà',
 'bà',
 'ấy',
 'bài',
 'bài',
 'bác',
 'bài',
 'bỏ',
 'bài',
 'cái',
 'bác',
 'bán',
 'bán',
 'cấp',
 'bán',
 'dạ',
 'bán',
 'thế',
 'bây',
 'bẩy',
 'bây',
 'chừ',
 'bây',
 'giờ',
 'bây',
 'nhiêu',
 'bèn',
 'béng',
 'bên',
 'bên',
 'bị',
 'bên',
 'có',
 'bên',
 'cạnh',
 'bông',
 'bước',
 'bước',
 'khỏi',
 'bước',
 'tới',
 'bước

- Not alphabet removing

In [10]:
training_data = []
for d in text_data:
  sent = []
  for word in d.split(" ") :
          if (word not in stop_word) :
              if ("_" in word) or (word.isalpha() == True):
                  sent.append(word)
  training_data.append(" ".join(sent))

In [11]:
training_data

['học_sinh học điều_kiện tạm_bợ nlđ học_sinh trường tiểu_học đống đa p bình_thạnh tphcm gởi học tạm km trường xuống_cấp trầm_trọng kế_hoạch năm_học trường tiểu_học đống đa khởi_công xây_dựng chỗ học năm_học kết_thúc xây trường phụ_huynh cảm_thấy yên_tâm hằng con_em học tình_trạng trường lớp tạm_bợ đi_lại kém an_toàn',
 'ngầm_hóa công_trình hạ_tầng kỹ_thuật ubnd tp chấp_thuận giao khu quản_lý giao_thông đô_thị phối_hợp đơn_vị quản_lý chuyên_ngành di_dời tái_lập công_trình hạ_tầng kỹ_thuật phạm_vi qui_hoạch xây_dựng dự_án phương_án ngầm_hóa riêng_biệt công_trình cáp_quang bưu_điện truyền_thông điện_lực cấp_nước ubnd tp chấp_thuận bưu_điện tp nghiên_cứu đầu_tư khai_thác xây_dựng đường_ống ngầm kỹ_thuật cáp_quang bưu_điện',
 'vấn_đề tuyển_sinh đh cđ phương_án tuyển_sinh đại_học cao_đẳng đh cđ giáo_dục đào_tạo gd đt công_bố chính_thức hội_nghị tuyển_sinh vừa_qua một_số vấn_đề trắc_nghiệm môn ngoại_ngữ thưởng đối_với học_sinh hs tốt_nghiệp ptth giỏi thay_đổi phương_án tuyển_sinh tuy_nhiên mộ

## 2. Extracting features
- tfidf calculating

In [12]:
tf = TfidfVectorizer(min_df=5,max_df=0.8,max_features=3000,sublinear_tf=True)
tf.fit(training_data)
X = tf.transform(training_data)

In [13]:
X.shape

(5000, 3000)

## 3. Classification algorithms | Naive Bayes - SVM

- Convert label from str to number

In [14]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
label_training = le.fit_transform(label_data)

len(label_training)

5000

In [15]:
len(set(label_training))

10

In [16]:
label_training

array([0, 0, 0, ..., 8, 8, 8], dtype=int64)

- Split data: train & validation

In [17]:
from sklearn.model_selection import train_test_split

X_train, X_valid, y_train, y_valid = train_test_split(training_data, label_training, test_size=0.2, random_state=38)

In [18]:
len(X_train)

4000

- Naive Bayes: - Train model

In [19]:
text_clf = Pipeline([('vect', CountVectorizer()), ('tfidf', TfidfTransformer()), ('clf', MultinomialNB())])

text_clf1 = text_clf.fit(X_train, y_train)

In [20]:
text_clf1

Pipeline(steps=[('vect', CountVectorizer()), ('tfidf', TfidfTransformer()),
                ('clf', MultinomialNB())])

- Test accuracy: Naive Bayes

In [21]:
text_clf.score(X_valid, y_valid)

0.874

- SVM: - Training

In [22]:
text_clf_svm = Pipeline([('vect', CountVectorizer()), ('tfidf', TfidfTransformer()),
                         ('clf-svm', SGDClassifier(loss='hinge', penalty='l2',alpha=1e-3, max_iter=5, random_state=42))])

text_clf_svm = text_clf_svm.fit(X_train, y_train)

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\linear_model\_stochastic_gradient.py:573: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  ConvergenceWarning)


- Test accuracy: SVM

In [23]:
predicted_svm = text_clf_svm.predict(X_valid)
np.mean(predicted_svm == y_valid)

0.882

## 4. Classify

- Load  data

In [24]:
with open('testing.txt', encoding='utf8') as file:
    data1 = file.read()

In [25]:
data_test_split = data1.split('\n')

len(data_test_split)

5000

In [26]:
data_test_split

['Máy điều hoà Funiki Từ đầu tháng 7, công ty nhựa và điện lạnh Hoà Phát tung ra thị trường sản phẩm mới là điều hoà tủ đứng và điều hoà âm trần hiệu Funiki. Đây cũng là những sản phẩm có công suất lớn và nhiều tính năng vượt trội. Hai loại sản phẩm này đều có chế độ ngủ vận hành tự động, tự điều chỉnh nhiệt độ tăng hoặc giảm theo mong muốn của bạn 1oC sau 1 giờ và tiếp 1oC sau 2 giờ và dừng lại cho đến khi căn phòng có nhiệt độ lý tưởng nhất. Cánh tự động đảo gió, làm lạnh và nóng trong thời gian ngắn, điều khiển từ xa dạ quang, tự động phá băng, khởi động từ bảo vệ máy nén, dễ dàng bảo dưưỡng. Đặc biệt, điều hòa còn có hệ thống lọc không khí ba lớp có bộ tinh lọc không khí ngăn lại những hạt bụi li ti, khử mùi khói thuốc lá và các chất gây ô nhiễm thông thường khác. Nó còn ngăn các vi rút, vi khuẩn cực nhỏ làm chúng trở nên vô hại và ngăn cản lây lan bệnh. Điều hòa dạng tủ đứng (Floor type): Lại 24000 BTU (một chiều giá 15 triệu 700 nghìn đồng và hai chiều giá 16 triệu 700 nghìn đồng

- Predict label

In [27]:
predicted = text_clf.predict(data_test_split)

predicted_label = le.inverse_transform(predicted)

len(predicted_label)

5000

In [28]:
predicted_label

array(['__KH__', '__DS__', '__PL__', ..., '__SK__', '__CTXH__',
       '__CTXH__'], dtype='<U8')

- Write to file: predicts.txt

In [29]:
with open('predicts.txt', 'w') as f:
    for item in predicted_label:
        f.write("%s\n" % item)

- draft

In [30]:
# text_data1 =[]
# for i in range(len(data_test_split)):
# #     e = data_test_split[i].replace(label_data[i], "")
# #     e = e.replace('\t', '')
#     text_lower = data_test_split[i].lower()
#     text_token = ViTokenizer.tokenize(text_lower)
#     text_data1.insert(i, text_token)
    
# len(text_data1)

# test_data1 = []
# for d in text_data1:
#   sent = []
#   for word in d.split(" ") :
#           if (word not in stop_word) :
#               if ("_" in word) or (word.isalpha() == True):
#                   sent.append(word)
#   test_data1.append(" ".join(sent))

# test_data1


# predicted = text_clf.predict(test_data1)

# predicted[100]